In [1]:
import pandas as pd
import re
import collections
from sklearn.model_selection import train_test_split
from sklearn.metrics import precision_recall_fscore_support
from nltk.corpus import stopwords
import numpy as np

In [2]:
data_df = pd.read_csv("data/training/data_train.csv", dtype='unicode')
data_df.fillna(value='', inplace=True)
data_df = data_df.apply(lambda x: x.astype(str).str.lower())

In [3]:
data_df[['clarity','conciseness']] = data_df[['clarity','conciseness']].apply(pd.to_numeric)

In [4]:
def cleanhtml(raw_html):
    result = re.sub(re.compile('<.*?>'), ' ', raw_html)
    return result
data_df['short_description_clear_html'] = data_df.apply(lambda row: cleanhtml(row['short_description']), axis=1)

In [5]:
train_df, test_df = train_test_split(data_df, test_size = 0.2)

In [6]:
full_categories_set = set()

In [7]:
for index, row in train_df.iterrows():
    full_category = row['category_lvl_1'] + "_" + row['category_lvl_2'] \
        + "_" + row['category_lvl_3']
    full_categories_set.add(full_category)

In [8]:
def create_bag_of_word(texts):
    return [ collections.Counter(re.findall(r'\w+', txt)) for txt in texts]

In [9]:
categories_word_most_frequence_dict = {}
categories_word_un_clarity_most_frequency_dict = {}
# categories_description_most_frequence_dict = {}

stopwords_set = set(stopwords.words('english'))

for full_category in full_categories_set:        

    categories = full_category.split(sep="_", maxsplit = 3)
    category_level_1 = categories[0]
    category_level_2 = categories[1]
    category_level_3 = categories[2]
    
    product_by_category = train_df[(train_df.category_lvl_1 == category_level_1) &
                                   (train_df.category_lvl_2 == category_level_2) &
                                   (train_df.category_lvl_3 == category_level_3) &
                                   (train_df.clarity == 1)]
    bag_of_words_title = create_bag_of_word([product_by_category.title.str.cat(sep=' ')])
  
    most_common_words = []
    for word, count in bag_of_words_title[0].most_common():           
        if (count > 10) & (not word.isnumeric()) & (word not in stopwords_set):
            if category_level_1 == "fashion":
                if word not in ['women', 'womens', 'girl', 'girls', 'woman'] and (count > 20):
                    most_common_words.append(word)
            else:
                most_common_words.append(word)
    
    categories_word_most_frequence_dict[full_category] = most_common_words
    
    ##------------ create dict for unclarify product -------------#######
    

    unclarity_product_by_category = train_df[(train_df.category_lvl_1 == category_level_1) &
                                   (train_df.category_lvl_2 == category_level_2) &
                                   (train_df.category_lvl_3 == category_level_3) &
                                   (train_df.clarity == 0)]
    bag_of_words_title = create_bag_of_word([unclarity_product_by_category.title.str.cat(sep=' ')])
  
    most_common_words = []
    for word, count in bag_of_words_title[0].most_common():           
        if (count > 10) & (not word.isnumeric()) & (word not in stopwords_set):
            if category_level_1 == "fashion":
                if word not in ['women', 'womens', 'girl', 'girls', 'woman'] and (count > 20):
                    most_common_words.append(word)
            else:
                most_common_words.append(word)
    
    categories_word_un_clarity_most_frequency_dict[full_category] = most_common_words

# Test model

In [10]:
clarities_pred = np.zeros(len (test_df))
categories_word_wrong_case_dict = {}

i = 0
for index, row in test_df.iterrows():
    
    full_category = row['category_lvl_1'] + "_" + row['category_lvl_2'] \
        + "_" + row['category_lvl_3']
    most_common_words_title = categories_word_most_frequence_dict.get(full_category)
    most_common_words_unclarity = categories_word_un_clarity_most_frequency_dict.get(full_category)

    nb_of_match_word = 0
    for word in row['title'].split():
        if word in most_common_words_title:
            nb_of_match_word += 1
            
            
    nb_of_match_unclarity = 0
    for word in row['title'].split():
        if word in most_common_words_unclarity:
            nb_of_match_unclarity += 1
            
    
    if (nb_of_match_word == 0) & (nb_of_match_unclarity == 0):
        clarities_pred[i] = 0.5
    elif (nb_of_match_word > 0) & (nb_of_match_unclarity > 0) :
        clarities_pred[i] = nb_of_match_word * 1.0 / (nb_of_match_word + nb_of_match_unclarity)
    elif (nb_of_match_word > 0) & (nb_of_match_unclarity == 0):
        clarities_pred[i] = 1
    elif (nb_of_match_word == 0) & (nb_of_match_unclarity > 0):
        clarities_pred[i] = 0

    print("i = ", i)
    print ("title: ", row['title'])
#     print ("descirpiton: ", row['short_description'])
    print ("full_category: ", full_category)
    print ("clarities_pred[i]: ", clarities_pred[i])
    print ("actual: ", row['clarity'])
    print("clarity match: ", nb_of_match_word)
    print("unclarity match: ", nb_of_match_unclarity)
    
    
    if clarities_pred[i] != row['clarity']:
        if categories_word_wrong_case_dict.get(full_category) == None:
            categories_word_wrong_case_dict[full_category] = 0
        categories_word_wrong_case_dict[full_category] += 1
    
    i = i + 1   
    

i =  0
title:  ge new fashion dw design geneva watch women pu leather strap quartz watches  (pink) (intl)
descirpiton:  <p>   </p><p>  </p><ul><li>100% brand new</li><li>fashion</li><li>high quality</li></ul><p>   </p><p>   </p><p> </p><p></p>
full_category:  watches sunglasses jewellery_watches_women
clarities_pred[i]:  0.5
actual:  1
clarity match:  11
unclarity match:  7
i =  1
title:  health paradise organic turmeric powder 100g
descirpiton:  <ul> <li>aids in fat metabolism and weight management</li> <li>lowers cholesterol</li> <li>helps in prevent gas / bloating</li> </ul> 
full_category:  health & beauty_food supplements_well being
clarities_pred[i]:  1.0
actual:  1
clarity match:  1
unclarity match:  0
i =  2
title:  2016 fashion women lace up suede leather skirt sexy high waist bodycon skirts womens vintage pocket short pencil skirt faldas = size: m = color: pink
descirpiton:  gender: women / patterntype: solid / silhouette: pencil / dresseslength: aboveknee mini / decoration: 

title:  protective pu leather case with belt clip for iphone 6 4.7" black
descirpiton:  <ul> <li>quantity: 1 piece</li> <li>material: pu leather</li> <li>compatible models: iphone 6</li> <li>style: full body cases, flip open</li> <li>design: solid color, with clips</li> </ul> 
full_category:  mobiles & tablets_accessories_phone cases
clarities_pred[i]:  1.0
actual:  1
clarity match:  6
unclarity match:  0
i =  93
title:  10 metres bubble wrap (10m x 50cm) - 10mm small bubble
descirpiton:  <div> <ul> <li>length: 10m, width: 50cm</li> <li>bubble size: 10mm</li> <li>ready stock in sg</li> <li>versatile, multi-use</li> </ul> </div> 
full_category:  home & living_stationery_novelty
clarities_pred[i]:  0.5
actual:  1
clarity match:  0
unclarity match:  0
i =  94
title:  new english carved waterproof removable wall stickers
descirpiton:  <ul> <li>high quality</li> <li>brand new</li> <li>easy to use</li> </ul> 
full_category:  home & living_home décor_wall art
clarities_pred[i]:  1.0
actual:  

actual:  1
clarity match:  9
unclarity match:  3
i =  248
title:  women winter gloves new touch screen thermal mittens female outdoor thick fleece warm gloves (black)
descirpiton:  <div> <ul> <li>100% brand new and high quality</li> <li>easy and convenient to carry and use</li> <li>soft lined,very comfortable to wear</li> <li>perfect accessory to keep your hands warm during the cold winter season</li> </ul> </div> 
full_category:  fashion_women_accessories
clarities_pred[i]:  1.0
actual:  1
clarity match:  3
unclarity match:  0
i =  249
title:  classic crocodile pattern cowhide leather long design women wallet genuine leather japanned female wallet (yellow)
descirpiton:  <div> <ul> <li>100% brand new and high quality</li> <li>a fashionable and durable wallet</li> <li>designed to hold cash, cards and other little things</li> <li>you can simply hold it on hand or put it in bag</li> <li>enough to fit for your various dress</li> </ul> </div> 
full_category:  fashion_women_wallets & accesso

descirpiton:  <ul> <li>100% new high quality case. made of good synthetic leather , very durable</li> <li>includes slots to store your credit cards / business cards</li> <li>with a stand to prop up your phone while you watch movies, read ebooks or watch presentations</li> <li>made of high quality colorful pu leather and magnetic clip design</li> <li>this stylish design make your phone more attractive and provides the maximum protection against scratches and scuffs</li> </ul> 
full_category:  mobiles & tablets_accessories_phone cases
clarities_pred[i]:  1.0
actual:  1
clarity match:  13
unclarity match:  0
i =  396
title:  electrolux 90cm slim hood eft9516x free kuchen induction cooker
descirpiton:  <ul> <li>550 m3/h</li> <li>exhausted /recirculated</li> <li>push button with pilot light</li> </ul> <ul> <li>product is not eligible for vouchers</li> </ul> 
full_category:  home appliances_large appliances_hoods
clarities_pred[i]:  1.0
actual:  1
clarity match:  1
unclarity match:  0
i =  3

descirpiton:  <ul> <li> <p>100% brand new.</p> </li> </ul> <ul> <li> <p>material: cotton blend</p> </li> </ul> <ul> <li> <p>4 colors for your choice: purple, gray, green, black</p> </li> </ul> <ul> <li> <p>occasion: casual, beach</p> </li> </ul> <ul> <li> <p>sleeveless, long dress</p> </li> </ul> <ul> <li> <p>size: there are three sizes (m , l, and xl) available for the following listing. please allow 1-2cm differs due to manual measurement, thanks (all measurement in cm and please note 1cm=0.39inch</p> </li> </ul> <ul> <li> <p>hint for choosing proper size:1. use similar clothing to compare with the size.</p> </li> </ul> <ul> <li> <p>2. choose larger sizes if your size are same as the flat measurement size chart.</p> </li> </ul> <ul> <li> <p>attention:1.please ignore the tag size comes with the cloth. the tag size sometimes can be a larger than our description size because those are for chinese. we are 1 or 2 sizes smaller than european and american people.</p> </li> </ul> <ul> <li> <

...

i =  6652
title:  moonmini tpu back phone case cover skin protector for samsung galaxy a3/a3000 (export)
descirpiton:  <ul><li>premium look and feel</li> <li>perfect and attractive decorate your phone</li> <li>protect your phone from scratches/shock and dust</li> <li>elegant design and excellent quality</li> <li>durable and fashionable</li> <li>all round protection</li> <li>easy to use: just snap it on and snap it off</li> <li>unique case just for you</li></ul>
full_category:  mobiles & tablets_accessories_phone cases
clarities_pred[i]:  1.0
actual:  1
clarity match:  10
unclarity match:  0
i =  6653
title:  10cc rma-223 soldering flux set of 2
descirpiton:  <ul> <li>volume: 10cc</li> <li>flux type: rma-223</li> <li>used for soldering bga icswith hotair reflow&nbsp;</li> <li>viscosity: 0.01 pa·s</li> <li>activity: neutral</li> <li>melting point: 150</li> </ul> 
full_category:  computers & laptops_computer accessories_gadgets
clarities_pred[i]:  0.5
actual:  1
clarity match:  0
unclarit

descirpiton:  <ul><li></li><li>brand new</li><li>price cost-effective</li><li>quality reliable</li><li>durable</li></ul>
full_category:  home & living_bath_bathroom accessories
clarities_pred[i]:  1.0
actual:  1
clarity match:  4
unclarity match:  0
i =  6772
title:  fujidenzo 11.0 cu.ft sliding glass top chest freezer fd-11 adf (white)
descirpiton:  <ul> <li>11 cu.ft. glass top chest freezers</li> <li>220v/280w</li> <li>eer: 197</li> <li>dual function/clean back design</li> <li>frontal temperature control/frontal drain</li> <li>aluminum inner lining/roller feet</li> <li>key lock/ 2 wire baskets</li> </ul> 
full_category:  home appliances_large appliances_freezers
clarities_pred[i]:  1.0
actual:  1
clarity match:  2
unclarity match:  0
i =  6773
title:  *20 units combo pack*compatible laser toner cartridge q5949a / 49a / q5949 / 5949a / laserjet / laser jet / 1160 / 1320 / 1320n / 1320nw / 1320w / 1320tn / 1321 / 3390 / 3392
descirpiton:  <ul style= "padding: 0px 40px; font-family: san

descirpiton:  <ul style= "color: rgb(80, 82, 85); font-family: myriadprolight, helvetica, arial, sans-serif; font-size: 18px; line-height: 23.4px; margin: 0px; padding: 0px; border: none;"> <li style= "margin: 0px 0px 0.5em; padding: 0px 0px 0px 15px; border: none; list-style: none; background: url(&quot;http://uk.tp-link.com/res/style/images/list-style-image-highlights.gif&quot;) 0px 0.5em no-repeat;"> tpcamera app - use the tpcamera app to access feeds from anywhere, at any time</li> <li style= "margin: 0px 0px 0.5em; padding: 0px 0px 0px 15px; border: none; list-style: none; background: url(&quot;http://uk.tp-link.com/res/style/images/list-style-image-highlights.gif&quot;) 0px 0.5em no-repeat;"> motion detection - immediate notification by email or ftp whenever motion is detected</li> <li style= "margin: 0px 0px 0.5em; padding: 0px 0px 0px 15px; border: none; list-style: none; background: url(&quot;http://uk.tp-link.com/res/style/images/list-style-image-highlights.gif&quot;) 0px 0.5

clarities_pred[i]:  1.0
actual:  1
clarity match:  7
unclarity match:  0
i =  7030
title:  kolin kdm-20dgs 20l/day dehumidifier (white)
descirpiton:  <ul> <li>removes harmful high water content in the air</li> <li>430 watts&nbsp;</li> <li>power: 220v, 60hz&nbsp;</li> <li>extraction rate: 20 liters/day&nbsp;</li> <li>room size: 25-40 sqm</li> </ul> <ul style="list-style-type: decimal;"></ul> 
full_category:  home appliances_cooling & heating_air purifiers, dehumidifiers & humidifiers
clarities_pred[i]:  0.5
actual:  1
clarity match:  0
unclarity match:  0
i =  7031
title:  shirt sleeve cardigan (beige)
descirpiton:  <ul> <li>edition type: slim</li> <li>main fabric: cotton</li> <li>fabric main ingredients content: 70 (%)</li> <li>it contains gross amount: 70% or more</li> </ul> 
full_category:  fashion_women_clothing
clarities_pred[i]:  0.5
actual:  1
clarity match:  3
unclarity match:  2
i =  7032
title:  fashion women's casual shoes w4-1213-black - intl
descirpiton:  <ul> <li>comfortab

full_category:  cameras_gadgets & other cameras_car cameras
clarities_pred[i]:  1.0
actual:  1
clarity match:  10
unclarity match:  0
i =  7192
title:  37mm metal tilted vented lens hood shade for leica m
descirpiton:  <ul> <li>hood size: 37mm</li> <li>hood material: matel</li> <li>hood color: black</li> </ul> 
full_category:  cameras_lenses_
clarities_pred[i]:  1.0
actual:  1
clarity match:  1
unclarity match:  0
i =  7193
title:  hard pc back case for iphone 5/5s (multicolor)
descirpiton:  <div> <ul> <li>snug fit lightweight and protective.</li> <li>cut outs allow access to charge port and speakers.</li> <li>automatically wake and put to sleep your device.</li> <li>synthetic exterior and smooth interior for protection.</li> <li>easy to install and remove.;</li> </ul> </div> 
full_category:  mobiles & tablets_accessories_phone cases
clarities_pred[i]:  1.0
actual:  1
clarity match:  5
unclarity match:  0
i =  7194
title:  5pcs different sizes precision flat blade slotted screw driver 

In [11]:
from sklearn.metrics import mean_squared_error
np.sqrt(mean_squared_error(test_df.clarity.as_matrix(), clarities_pred))

0.30784828463015884

In [12]:
max(categories_word_wrong_case_dict, key=categories_word_wrong_case_dict.get)

'fashion_women_clothing'

In [13]:
categories_word_wrong_case_dict

{'cameras_camera accessories_camera cases, covers and bags': 2,
 'cameras_camera accessories_lighting & studio equipment': 2,
 'cameras_camera accessories_sports & action camera accessories': 3,
 'cameras_camera accessories_tripods & monopods': 1,
 'cameras_drones_': 2,
 'cameras_gadgets & other cameras_car cameras': 1,
 'cameras_gadgets & other cameras_security cameras': 1,
 'cameras_lenses_': 6,
 'cameras_lenses_lens accessories': 1,
 'cameras_lenses_mirrorless lenses': 3,
 'cameras_mirrorless_': 1,
 'cameras_point & shoot_point & shoot': 2,
 'cameras_video & action camcorder_sports & action camera': 2,
 'computers & laptops_computer accessories_battery adaptors': 2,
 'computers & laptops_computer accessories_gadgets': 10,
 'computers & laptops_computer accessories_gaming headphones': 2,
 'computers & laptops_computer accessories_mac accessories': 1,
 'computers & laptops_computer accessories_mice': 1,
 'computers & laptops_computer accessories_monitors': 1,
 'computers & laptops_com